# Marqo Demo

Based off of Jesse's Simple Wiki Demo and Li's Vit-L-14-coco-2017 trials.

There are three types of search we would like to conduct:

> 1. Text to Image
> 2. Image to Image
> 3. Image to Text



In [1]:
#####################################################
### STEP 0. Import and define any helper functions
#####################################################

# Load libraries in
# %matplotlib inline
# from pycocotools.coco import COCO
import numpy as np
#import pylab
# import glob
import os
from marqo import Client
from marqo.errors import MarqoApiError
import torch
import pandas as pd
import json
import pprint
import math
import copy
import requests
import shutil # save img locally
import multiprocessing as mp
from multiprocessing import Pool
import PIL
from PIL import Image
import threading
from cairosvg import svg2png

/root/.cache/pypoetry/virtualenvs/marqo-overall-demo-4I8VLaeb-py3.9/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Simple Wikipedia Dataset loading

In [54]:
# Helper functions
def read_json(filename: str) -> dict:
    # reads a json file
    with open(filename, 'r', encoding='utf-8') as f:
        data = json.load(f)
    return data

def replace_title(data: dict) -> dict:
    # removes the wikipedia from the title for better matching
    data['title'] = data['title'].replace('- Wikipedia', '')
    return data

def add_id(data: dict, id_num) -> dict:
    # adds _id to the json file
    data['_id'] = str(id_num)
    return data

def split_big_docs(data, field='content', char_len=5e4):
    # there are some large documents which can cause issues for some users
    new_data = []
    for dat in data:
        
        content = dat[field]
        N = len(content)
        
        if N >= char_len:
            n_chunks = math.ceil(N / char_len)
            new_content = np.array_split(list(content), n_chunks)
            
            for _content in new_content:
                new_dat = copy.deepcopy(dat)
                new_dat[field] = ''.join(_content)
                new_data.append(new_dat)
        else:
            new_data.append(dat)
    return new_data

def fetch_image_url(article_title):
    params = {
        'action': 'query',
        'format': 'json',
        'titles': article_title,
        'prop': 'pageimages',
        'piprop': 'original'
    }
 
    response = requests.get("https://wikipedia.org/w/api.php", params=params)
    json_data = response.json()
    
    #print("JSON DUMP: ", json_data)
    if next(iter(json_data['query']['pages'])) == '-1':
        # Page/Article no longer exists.
        return -1
    
    page = next(iter(json_data['query']['pages'].values()))
    
    if 'original' in page:
        image_url = page['original']['source']
        return image_url
    else:
        # Page has no image
        return -2


In [57]:
%%time
#####################################################
### STEP 1. load the data
#####################################################

# get the data
dataset_file = "large_assets/simplewiki.json"
data = read_json(dataset_file)

# clean up the title and add id
for i in range(len(data)):
    data[i] = add_id(data[i], i)
    data[i] = replace_title(data[i])

# split big ones to make it easier for users on all hardware
data = split_big_docs(data)
print(f"loaded data with {len(data)} entries")

loaded data with 188636 entries
CPU times: user 2.76 s, sys: 1.15 s, total: 3.91 s
Wall time: 4.19 s


In [58]:
data

[{'title': 'April ',
  'url': 'http://s.wikipedia.org/wiki/April',
  'domain': 's.wikipedia.org',
  'content': 'April is the fourth month of the year, and comes between March and May. It is one of four months to have 30 days.\r\rApril always begins on the same day of week as July, and additionally, January in leap years. April always ends on the same day of the week as December.\r\rApril\'s flowers are the Sweet Pea and Daisy. Its birthstone is the diamond. The meaning of the diamond is innocence.\r\rThe Month \rSpring flowers in April in the Northern Hemisphere.\rApril comes between March and May, making it the fourth month of the year. It also comes first in the year out of the four months that have 30 days, as June, September and November are later in the year.\r\rApril begins on the same day of the week as July every year and on the same day of the week as January in leap years. April ends on the same day of the week as December every year, as each other\'s last days are exactly 35

## Index Properties per Model

In [3]:
model_data = {
    # Unused, until we index wimple wiki images
    "clip-simple-wiki": {
        "model": "ViT-L/14",
        "non_tensor_fields": ["title", "content", "url", "domain", "docDate"],
        "searchable_attributes": ["image"]
    },
        
    "sbert-simple-wiki": {
        "model": "onnx/all_datasets_v4_MiniLM-L6",
        "searchable_attributes": ["title", "content"],
        "non_tensor_fields": ["image", "url", "domain", "docDate"],
    },
    
    # Focus is the image itself, not the article. We can say the focus is the SECTION
    "sbert-wit": {
        "model": "onnx/all_datasets_v4_MiniLM-L6",
        # Top 4 searchable attributes
        "searchable_attributes": ["page_title", "section_title", "caption_attribution_description", "context_section_description"],
        "non_tensor_fields": ["image_url", "hierarchical_section_title", "caption_reference_description", "caption_alt_text_description", "context_page_description"],
    },
    
    "clip-bored-apes": {
        "model": "ViT-L/14",
        "non_tensor_fields": ["title", "content", "url", "domain", "docDate"],
        "searchable_attributes": ["image"]
    },
}

index_name_prefix = "marqo-overall-demo"
device = "cuda"

## Demo Part 1: SBERT Simple Wiki Index

In [4]:
%%time
index_type = "sbert-simple-wiki"
index_name = index_name_prefix + "-" + index_type
client = Client()

CPU times: user 102 µs, sys: 67 µs, total: 169 µs
Wall time: 173 µs


In [20]:
%%time
# Create the SBERT simple wiki Index
index_type = "sbert-simple-wiki"
client.create_index(index_name, model=model_data[index_type]["model"])

model_data[index_type]["responses"] = client.index(index_name).add_documents(data, 
                                                                     device=device,
                                                                     client_batch_size = 20, 
                                                                     non_tensor_fields = model_data[index_type]["non_tensor_fields"])

2022-12-01 19:53:47,433 logger:'marqo' INFO starting batch ingestion with batch size 20
2022-12-01 19:56:04,196 logger:'marqo' INFO batch 0: ingested 20 docs. Time taken: 0:02:16.708261. Average timer per doc 0:00:06.835413
2022-12-01 19:56:05,953 logger:'marqo' INFO batch 1: ingested 20 docs. Time taken: 0:00:01.756439. Average timer per doc 0:00:00.087822
2022-12-01 19:56:06,935 logger:'marqo' INFO batch 2: ingested 20 docs. Time taken: 0:00:00.981470. Average timer per doc 0:00:00.049074
2022-12-01 19:56:08,086 logger:'marqo' INFO batch 3: ingested 20 docs. Time taken: 0:00:01.150801. Average timer per doc 0:00:00.057540
2022-12-01 19:56:09,061 logger:'marqo' INFO batch 4: ingested 20 docs. Time taken: 0:00:00.973613. Average timer per doc 0:00:00.048681
2022-12-01 19:56:10,220 logger:'marqo' INFO batch 5: ingested 20 docs. Time taken: 0:00:01.158681. Average timer per doc 0:00:00.057934
2022-12-01 19:56:11,078 logger:'marqo' INFO batch 6: ingested 20 docs. Time taken: 0:00:00.85750

2022-12-01 19:57:47,793 logger:'marqo' INFO batch 60: ingested 20 docs. Time taken: 0:00:01.519697. Average timer per doc 0:00:00.075985
2022-12-01 19:57:49,494 logger:'marqo' INFO batch 61: ingested 20 docs. Time taken: 0:00:01.698909. Average timer per doc 0:00:00.084945
2022-12-01 19:57:49,951 logger:'marqo' INFO batch 62: ingested 20 docs. Time taken: 0:00:00.455668. Average timer per doc 0:00:00.022783
2022-12-01 19:57:50,980 logger:'marqo' INFO batch 63: ingested 20 docs. Time taken: 0:00:01.029155. Average timer per doc 0:00:00.051458
2022-12-01 19:57:52,429 logger:'marqo' INFO batch 64: ingested 20 docs. Time taken: 0:00:01.447797. Average timer per doc 0:00:00.072390
2022-12-01 19:57:53,525 logger:'marqo' INFO batch 65: ingested 20 docs. Time taken: 0:00:01.095696. Average timer per doc 0:00:00.054785
2022-12-01 19:57:54,854 logger:'marqo' INFO batch 66: ingested 20 docs. Time taken: 0:00:01.327433. Average timer per doc 0:00:00.066372
2022-12-01 19:57:55,885 logger:'marqo' IN

2022-12-01 19:58:52,405 logger:'marqo' INFO batch 120: ingested 20 docs. Time taken: 0:00:01.320371. Average timer per doc 0:00:00.066019
2022-12-01 19:58:53,748 logger:'marqo' INFO batch 121: ingested 20 docs. Time taken: 0:00:01.342366. Average timer per doc 0:00:00.067118
2022-12-01 19:58:58,521 logger:'marqo' INFO batch 122: ingested 20 docs. Time taken: 0:00:04.772474. Average timer per doc 0:00:00.238624
2022-12-01 19:58:59,472 logger:'marqo' INFO batch 123: ingested 20 docs. Time taken: 0:00:00.949351. Average timer per doc 0:00:00.047468
2022-12-01 19:59:00,031 logger:'marqo' INFO batch 124: ingested 20 docs. Time taken: 0:00:00.557996. Average timer per doc 0:00:00.027900
2022-12-01 19:59:00,490 logger:'marqo' INFO batch 125: ingested 20 docs. Time taken: 0:00:00.458778. Average timer per doc 0:00:00.022939
2022-12-01 19:59:01,601 logger:'marqo' INFO batch 126: ingested 20 docs. Time taken: 0:00:01.109885. Average timer per doc 0:00:00.055494
2022-12-01 19:59:02,424 logger:'ma

2022-12-01 20:00:45,835 logger:'marqo' INFO batch 180: ingested 20 docs. Time taken: 0:00:00.573780. Average timer per doc 0:00:00.028689
2022-12-01 20:00:46,300 logger:'marqo' INFO batch 181: ingested 20 docs. Time taken: 0:00:00.463615. Average timer per doc 0:00:00.023181
2022-12-01 20:00:47,119 logger:'marqo' INFO batch 182: ingested 20 docs. Time taken: 0:00:00.818868. Average timer per doc 0:00:00.040943
2022-12-01 20:00:48,071 logger:'marqo' INFO batch 183: ingested 20 docs. Time taken: 0:00:00.950726. Average timer per doc 0:00:00.047536
2022-12-01 20:00:48,542 logger:'marqo' INFO batch 184: ingested 20 docs. Time taken: 0:00:00.470134. Average timer per doc 0:00:00.023507
2022-12-01 20:00:50,124 logger:'marqo' INFO batch 185: ingested 20 docs. Time taken: 0:00:01.580898. Average timer per doc 0:00:00.079045
2022-12-01 20:00:51,088 logger:'marqo' INFO batch 186: ingested 20 docs. Time taken: 0:00:00.964318. Average timer per doc 0:00:00.048216
2022-12-01 20:00:51,502 logger:'ma

2022-12-01 20:01:49,752 logger:'marqo' INFO batch 240: ingested 20 docs. Time taken: 0:00:01.061851. Average timer per doc 0:00:00.053093
2022-12-01 20:01:50,835 logger:'marqo' INFO batch 241: ingested 20 docs. Time taken: 0:00:01.082239. Average timer per doc 0:00:00.054112
2022-12-01 20:01:52,066 logger:'marqo' INFO batch 242: ingested 20 docs. Time taken: 0:00:01.229963. Average timer per doc 0:00:00.061498
2022-12-01 20:01:52,728 logger:'marqo' INFO batch 243: ingested 20 docs. Time taken: 0:00:00.661660. Average timer per doc 0:00:00.033083
2022-12-01 20:01:53,379 logger:'marqo' INFO batch 244: ingested 20 docs. Time taken: 0:00:00.650334. Average timer per doc 0:00:00.032517
2022-12-01 20:01:54,014 logger:'marqo' INFO batch 245: ingested 20 docs. Time taken: 0:00:00.633400. Average timer per doc 0:00:00.031670
2022-12-01 20:01:54,699 logger:'marqo' INFO batch 246: ingested 20 docs. Time taken: 0:00:00.684971. Average timer per doc 0:00:00.034249
2022-12-01 20:01:56,794 logger:'ma

...

2022-12-01 21:18:24,681 logger:'marqo' INFO batch 9221: ingested 20 docs. Time taken: 0:00:00.352037. Average timer per doc 0:00:00.017602
2022-12-01 21:18:24,902 logger:'marqo' INFO batch 9222: ingested 20 docs. Time taken: 0:00:00.220355. Average timer per doc 0:00:00.011018
2022-12-01 21:18:25,116 logger:'marqo' INFO batch 9223: ingested 20 docs. Time taken: 0:00:00.212895. Average timer per doc 0:00:00.010645
2022-12-01 21:18:25,326 logger:'marqo' INFO batch 9224: ingested 20 docs. Time taken: 0:00:00.209195. Average timer per doc 0:00:00.010460
2022-12-01 21:18:25,550 logger:'marqo' INFO batch 9225: ingested 20 docs. Time taken: 0:00:00.223073. Average timer per doc 0:00:00.011154
2022-12-01 21:18:25,780 logger:'marqo' INFO batch 9226: ingested 20 docs. Time taken: 0:00:00.228837. Average timer per doc 0:00:00.011442
2022-12-01 21:18:26,152 logger:'marqo' INFO batch 9227: ingested 20 docs. Time taken: 0:00:00.371185. Average timer per doc 0:00:00.018559
2022-12-01 21:18:26,419 log

2022-12-01 21:18:48,933 logger:'marqo' INFO batch 9280: ingested 20 docs. Time taken: 0:00:00.687218. Average timer per doc 0:00:00.034361
2022-12-01 21:18:49,382 logger:'marqo' INFO batch 9281: ingested 20 docs. Time taken: 0:00:00.448328. Average timer per doc 0:00:00.022416
2022-12-01 21:18:49,708 logger:'marqo' INFO batch 9282: ingested 20 docs. Time taken: 0:00:00.324708. Average timer per doc 0:00:00.016235
2022-12-01 21:18:50,048 logger:'marqo' INFO batch 9283: ingested 20 docs. Time taken: 0:00:00.339547. Average timer per doc 0:00:00.016977
2022-12-01 21:18:50,325 logger:'marqo' INFO batch 9284: ingested 20 docs. Time taken: 0:00:00.276064. Average timer per doc 0:00:00.013803
2022-12-01 21:18:50,697 logger:'marqo' INFO batch 9285: ingested 20 docs. Time taken: 0:00:00.370740. Average timer per doc 0:00:00.018537
2022-12-01 21:18:51,007 logger:'marqo' INFO batch 9286: ingested 20 docs. Time taken: 0:00:00.309103. Average timer per doc 0:00:00.015455
2022-12-01 21:18:51,261 log

2022-12-01 21:19:33,713 logger:'marqo' INFO batch 9339: ingested 20 docs. Time taken: 0:00:00.405936. Average timer per doc 0:00:00.020297
2022-12-01 21:19:34,111 logger:'marqo' INFO batch 9340: ingested 20 docs. Time taken: 0:00:00.397804. Average timer per doc 0:00:00.019890
2022-12-01 21:19:34,717 logger:'marqo' INFO batch 9341: ingested 20 docs. Time taken: 0:00:00.605019. Average timer per doc 0:00:00.030251
2022-12-01 21:19:35,020 logger:'marqo' INFO batch 9342: ingested 20 docs. Time taken: 0:00:00.301637. Average timer per doc 0:00:00.015082
2022-12-01 21:19:35,407 logger:'marqo' INFO batch 9343: ingested 20 docs. Time taken: 0:00:00.386407. Average timer per doc 0:00:00.019320
2022-12-01 21:19:35,726 logger:'marqo' INFO batch 9344: ingested 20 docs. Time taken: 0:00:00.318196. Average timer per doc 0:00:00.015910
2022-12-01 21:19:35,986 logger:'marqo' INFO batch 9345: ingested 20 docs. Time taken: 0:00:00.259238. Average timer per doc 0:00:00.012962
2022-12-01 21:19:36,331 log

2022-12-01 21:19:53,210 logger:'marqo' INFO batch 9398: ingested 20 docs. Time taken: 0:00:00.280975. Average timer per doc 0:00:00.014049
2022-12-01 21:19:53,467 logger:'marqo' INFO batch 9399: ingested 20 docs. Time taken: 0:00:00.256771. Average timer per doc 0:00:00.012839
2022-12-01 21:19:53,748 logger:'marqo' INFO batch 9400: ingested 20 docs. Time taken: 0:00:00.279355. Average timer per doc 0:00:00.013968
2022-12-01 21:19:54,001 logger:'marqo' INFO batch 9401: ingested 20 docs. Time taken: 0:00:00.252416. Average timer per doc 0:00:00.012621
2022-12-01 21:19:54,272 logger:'marqo' INFO batch 9402: ingested 20 docs. Time taken: 0:00:00.271103. Average timer per doc 0:00:00.013555
2022-12-01 21:19:54,516 logger:'marqo' INFO batch 9403: ingested 20 docs. Time taken: 0:00:00.242473. Average timer per doc 0:00:00.012124
2022-12-01 21:19:54,748 logger:'marqo' INFO batch 9404: ingested 20 docs. Time taken: 0:00:00.231507. Average timer per doc 0:00:00.011575
2022-12-01 21:19:55,017 log

CPU times: user 51.2 s, sys: 3.96 s, total: 55.2 s
Wall time: 1h 26min 18s


## Search Phase

In [55]:
%%time

# Simple Wiki With SBERT
query = 'tallest animal on earth'
results = client.index(index_name).search(query, 
                                          device=device,
                                          searchable_attributes=model_data[index_type]["searchable_attributes"],
                                         )


result_num = 10
for i in range(result_num):
    print("RESULT: ", str(i))
    pprint.pprint(results['hits'][i]['title'])
    pprint.pprint(results['hits'][i]['_highlights'])
    print("Article at: ", results['hits'][i]['url'])
    
    display_image_url = fetch_image_url(results['hits'][i]['title'])
    if display_image_url == -1:
        print("Page/Article no longer exists.")
    elif display_image_url == -2:
        print("Page has no image.")
    else:
        print("Image at: ", fetch_image_url(results['hits'][i]['title']))
    print("")


# TODO: Find the image URL and display it. 
# How do we do lexical search? search_method='LEXICAL'

RESULT:  0
'Giraffe '
{'content': 'Giraffes are the tallest land animals on Earth, with necks that '
            'can be up to 2-2.4 m (6.6-7.9 ft) in length. Fully grown giraffes '
            'stand tall, with males taller than females.'}
Article at:  http://s.wikipedia.org/wiki/Giraffe
Image at:  https://upload.wikimedia.org/wikipedia/commons/9/9e/Giraffe_Mikumi_National_Park.jpg

RESULT:  1
'Giraffidae '
{'content': 'Giraffes are the tallest animal living on land, with a height of '
            'over 5 m. Okapis are smaller, only up to 2 m tall. '
            'Category:Even-toed ungulates'}
Article at:  http://s.wikipedia.org/wiki/Giraffidae
Image at:  https://upload.wikimedia.org/wikipedia/commons/6/67/Okapi.bristol.600pix.jpg

RESULT:  2
'Largest extinct animals '
{'title': 'Largest extinct animals'}
Article at:  http://s.wikipedia.org/wiki/Largest_extinct_animals
Page/Article no longer exists.

RESULT:  3
'List of tallest structures in the world '
{'title': 'List of tallest stru

## Demo Part 2: Bored Apes Image Search

In [48]:
file_name = "Qma1aZPn7iS1vxkfip6kjGjbA5EUPDaunsApJJ8mUt8pyT.png"
ipfs_url = "https://ipfs.io/ipfs/" + file_name.split('.')[0]
ipfs_url

'https://ipfs.io/ipfs/Qma1aZPn7iS1vxkfip6kjGjbA5EUPDaunsApJJ8mUt8pyT'

In [ ]:
img_id = 0
download_single_file(ipfs_url, "large_assets/images/ape_test/ape_" + str(img_id) + ".png", "png", img_id)

# OBSOLETE / TOOLS

# Approach 2: WIT Database

In [28]:
%%time

# add id with all the numbers
WIT_DATASET = "large_assets/wit_v1.train.all-1percent_sample.tsv"
raw_df = pd.read_csv(WIT_DATASET, sep='\t')
raw_df

CPU times: user 14.9 s, sys: 2.14 s, total: 17 s
Wall time: 18.2 s


language                                           page_url  \
0            es       https://es.wikipedia.org/wiki/Hoz_y_martillo   
1            de    https://de.wikipedia.org/wiki/Kleines_Hasenmaul   
2            ru  https://ru.wikipedia.org/wiki/%D0%A3%D0%BA%D1%...   
3            ru  https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%...   
4            sw  https://sw.wikipedia.org/wiki/Brookline,_Massa...   
...         ...                                                ...   
370368       en    https://en.wikipedia.org/wiki/Suillus_quiescens   
370369       fa  https://fa.wikipedia.org/wiki/%D8%A7%DA%A9%DB%...   
370370       de  https://de.wikipedia.org/wiki/Fauler_See_(Schw...   
370371       ko  https://ko.wikipedia.org/wiki/%EB%8C%80%ED%95%...   
370372       eo         https://eo.wikipedia.org/wiki/M%C3%B6nkloh   

                                                image_url  \
0       https://upload.wikimedia.org/wikipedia/commons...   
1       https://upload.wikimedia.org/wikipedia/commons...   
2       https://upload.wikimedia.org/wikipedia/commons...   
3       http://upload.wikimedia.org/wikipedia/commons/...   
4       https://upload.wikimedia.org/wikipedia/commons...   
...                                                   ...   
370368  https://upload.wikimedia.org/wikipedia/commons...   
370369  https://upload.wikimedia.org/wikipedia/commons...   
370370  http://upload.wikimedia.org/wikipedia/commons/...   
370371  https://upload.wikimedia.org/wikipedia/commons...   
370372  https://upload.wikimedia.org/wikipedia/commons...   

                             page_title                section_title  \
0                        Hoz y martillo                     Emblemas   
1                     Kleines Hasenmaul                          NaN   
2                     Украинская гривна  Изъятые из обращения монеты   
3       Менделеево (Московская область)                          NaN   
4              Brookline, Massachusetts                          NaN   
...                                 ...                          ...   
370368                Suillus quiescens     Habitat and distribution   
370369                        اکیر ترکی                          NaN   
370370            Fauler See (Schwerin)                          NaN   
370371                         대한출판문화협회                          NaN   
370372                          Mönkloh                       Bildoj   

                               hierarchical_section_title  \
0                     Hoz y martillo / Galería / Emblemas   
1                                       Kleines Hasenmaul   
2       Украинская гривна / Монеты / Изъятые из обраще...   
3                         Менделеево (Московская область)   
4                                Brookline, Massachusetts   
...                                                   ...   
370368       Suillus quiescens / Habitat and distribution   
370369                                          اکیر ترکی   
370370                              Fauler See (Schwerin)   
370371                                           대한출판문화협회   
370372                                   Mönkloh / Bildoj   

                            caption_reference_description  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4               Sehemu za Mji wa Brookline, Massachusetts   
...                                                   ...   
370368  S. quiescens forms mycorrhizal associations wi...   
370369                                                NaN   
370370                                                NaN   
370371                  고영수 회장 (2015 서울국제도서전 개최 기념 기자간담회)   
370372                                                NaN   

                          caption_attribution_description  \
0          Galego: Logo do Movemento Gale

In [29]:
raw_df.columns

Index(['language', 'page_url', 'image_url', 'page_title', 'section_title',
       'hierarchical_section_title', 'caption_reference_description',
       'caption_attribution_description', 'caption_alt_text_description',
       'mime_type', 'original_height', 'original_width', 'is_main_image',
       'attribution_passes_lang_id', 'page_changed_recently',
       'context_page_description', 'context_section_description'],
      dtype='object')

In [30]:
preproc_en_df = raw_df[raw_df["language"] == "en"][["image_url", 
                                                    "page_title",
                                                    "section_title", 
                                                    "hierarchical_section_title",
                                                    "caption_reference_description", 
                                                    "caption_attribution_description",
                                                    "caption_alt_text_description",
                                                    "context_page_description",
                                                    "context_section_description"
                                                   ]]

preproc_en_df.index = [i for i in range(len(preproc_en_df))]
preproc_en_df

image_url  \
0      http://upload.wikimedia.org/wikipedia/commons/...   
1      https://upload.wikimedia.org/wikipedia/commons...   
2      https://upload.wikimedia.org/wikipedia/commons...   
3      https://upload.wikimedia.org/wikipedia/commons...   
4      https://upload.wikimedia.org/wikipedia/commons...   
...                                                  ...   
54066  https://upload.wikimedia.org/wikipedia/commons...   
54067  http://upload.wikimedia.org/wikipedia/commons/...   
54068  http://upload.wikimedia.org/wikipedia/commons/...   
54069  https://upload.wikimedia.org/wikipedia/commons...   
54070  https://upload.wikimedia.org/wikipedia/commons...   

                                              page_title  \
0                                      Chinatown, Sydney   
1                                          Jayson Musson   
2                                     Euodynerus megaera   
3                                     Simon W. Rosendale   
4          List of National Natural Landmarks in Florida   
...                                                  ...   
54066  National Register of Historic Places listings ...   
54067                                             Varahi   
54068                                  Six-stroke engine   
54069                                         Yi Sun-sin   
54070                                  Suillus quiescens   

                    section_title  \
0          Bilingual street signs   
1                             NaN   
2                             NaN   
3                             NaN   
4      National Natural Landmarks   
...                           ...   
54066                         NaN   
54067                     Temples   
54068   Griffin six-stroke engine   
54069                Turtle Ships   
54070    Habitat and distribution   

                              hierarchical_section_title  \
0             Chinatown, Sydney / Bilingual street signs   
1                                          Jayson Musson   
2                                     Euodynerus megaera   
3                                     Simon W. Rosendale   
4      List of National Natural Landmarks in Florida ...   
...                                                  ...   
54066  National Register of Historic Places listings ...   
54067                         Varahi / Worship / Temples   
54068  Six-stroke engine / Engine types / Single-pist...   
54069  Yi Sun-sin / Military career / Japanese invasi...   
54070       Suillus quiescens / Habitat and distribution   

                           caption_reference_description  \
0                                                    NaN   
1                      Jayson Musson on October 29, 2007   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
54066                                                NaN   
54067             Central icon of Varahi Chaurasi temple   
54068         The Kerr engine at the Anson Engine Museum   
54069              Drawing of a 16th-century turtle ship   
54070  S. quiescens forms mycorrhizal associations wi...   

                         caption_attribution_description  \
0                        English: Hay Street 中文（繁體）‎: 禧街   
1       English: Jayson Scott Musson on October 29, 2007   
2                            English: Euodynerus megaera   
3      English: Simon Wolfe Rosendale (June 23, 1842 ...   
4      English: Photograph of Rainbow Springs in Mari...   
...                                                  ...   
54066  English: This modern hardware store is located...   
54067  English: ~ VARAHI above her Buffalo Vahana ~ c...   
54068  The Anson Engine Museum in Poynton, Cheshire c...   
54069  16th century Korean turtle ship in a depiction...   
54070  English: Pinus muricata at the Dundee Botanic ...  

## Downloading WIT Images

In [31]:
urls = list(preproc_en_df["image_url"])
headers = {
    "user-agent": "Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36"
}

In [33]:
%time
# DOWNLOADING IMAGES USING REQUESTS AND MULTIPROCESS
# TODO FLESH THIS OUT

urls = list(preproc_en_df["image_url"])
headers = {
    "user-agent": "Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36"
}


def download_and_convert_svg(url, file_name):
    svg = requests.get(url, headers=headers).text
    new_file_name = '.'.join(file_name.split('.')[:-1]) + '.png'
    svg2png(bytestring=svg, write_to=new_file_name)
    return True

    
def download_and_resize_image(url, file_name):
    # download the image and resize with PIL normally (jpg, png, gif).
    res = requests.get(url, headers=headers, stream = True)
    if res.status_code == 200:
        img = Image.open(res.raw)
        img.thumbnail((1024, 1024), Image.Resampling.LANCZOS)
        img.save(file_name)
        return True
    
    return False
    
def download_single_file(url, file_name, file_type, img_id):
    
    # If error occurs, output it but go on to the next files.
    try:
        if file_type == "svg":
            download_status = download_and_convert_svg(url, file_name)
        else:
            download_status = download_and_resize_image(url, file_name)
            
        # Keep track of failed downloads
        if not download_status:
            lock.acquire()
            print('HTTP Request: File ' + str(img_id) + ' Couldn\'t be retrieved')
            print('Offending File: ' + url + "\n")
            lock.release()
            
    except Exception as e:
        lock.acquire()
        print("Exception downloading as image: "+ str(img_id))
        print (e)
        print('Offending URL: ' + url + "\n")
        lock.release()
                    
    
def download_files(url_data):
    urls = url_data["urls"]
    
    # Iterate through each URL, and download the file
    for i in range(len(urls)):
        file_type = urls[i].split('.')[-1]
        img_id = url_data["start_id"] + i
        
        target_dir = 'large_assets/images/wit_v1.train.all-1percent_sample/'
        file_name = target_dir + str(img_id) + '.' + file_type
    
        # Check if image was already downloaded before trying it!
        if not os.path.exists(file_name):
            download_single_file(urls[i], file_name, file_type, img_id)
        else:
            # print('Already downloaded. Skipping: ', file_name)
            pass


def package_starting_ids(split_urls):
    # Label the IDs for the split URL lists
    final_url_data = []
    running_url_id = 0
    
    for i in range(len(split_urls)):
        final_url_data.append({
            "start_id": running_url_id,
            "urls": split_urls[i]
        })
        running_url_id += len(split_urls[i])
    return final_url_data

# Main image downloading code
n_processes = mp.cpu_count()
split_urls = np.array_split(urls, n_processes)
split_url_data = package_starting_ids(split_urls)

lock = mp.Lock()

with mp.Pool(processes = n_processes) as pool:
    results = pool.map(download_files, split_url_data)

# Not done. Will resume this some other time.
# TODO: Do we need to manually destroy the pool?

CPU times: user 3 µs, sys: 0 ns, total: 3 µs
Wall time: 5.01 µs
HTTP Request: File 45074 Couldn't be retrieved
Offending File: http://upload.wikimedia.org/wikipedia/commons/f/fc/Wappen_Schinne.png

HTTP Request: File 13549 Couldn't be retrieved
Offending File: http://upload.wikimedia.org/wikipedia/commons/1/1d/QT-2PCs_in_STAAF%2C_RVN_Hanger_c1968.jpg

HTTP Request: File 31545 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/d/da/AerialBaroboRiver.jpg

HTTP Request: File 27042 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/b/b7/Maerz1848_berlin.jpg

HTTP Request: File 40563 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/9/93/Tanker_Morris_2018c.jpg

HTTP Request: File 45096 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/9/9d/101_IOF-Stylized.jpg

HTTP Request: File 13599 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wi

Offending File: https://upload.wikimedia.org/wikipedia/commons/4/49/San_P%C3%A9dro_vue_baln%C3%A9aire.jpg

Exception downloading as image: 40858
EntitiesForbidden(name='ns_flows', system_id=None, public_id=None)
Offending URL: https://upload.wikimedia.org/wikipedia/commons/0/0e/CA1896House.svg

HTTP Request: File 36365 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/9/91/Horace_Newcomb_and_Alex_Trebek_%287268398640%29_%28cropped%29.jpg

Exception downloading as image: 13690
syntax error: line 1, column 0
Offending URL: https://upload.wikimedia.org/wikipedia/commons/2/29/Gadsden_Purchase_Cities_ZP.svg

HTTP Request: File 50100 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/a/ad/1953TornadoMemorial.jpg

HTTP Request: File 13783 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/a/a0/Pumapaparti.N.rao.jpg

HTTP Request: File 45522 Couldn't be retrieved
Offending File: http://upload


HTTP Request: File 23624 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/7/70/COVIDSafe_screenshot.jpg

HTTP Request: File 9652 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/7/71/Wall_painting_3_Abuna_Yemata_Guh.jpg

HTTP Request: File 32781 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/f/f1/Istiglal.jpg

HTTP Request: File 28395 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/1/10/Neiked_and_Miriam_Bryant.jpg

HTTP Request: File 14619 Couldn't be retrieved
Offending File: http://upload.wikimedia.org/wikipedia/commons/b/bc/Wappen_Druebeck.png

Exception downloading as image: 733
syntax error: line 1, column 0
Offending URL: https://upload.wikimedia.org/wikipedia/commons/f/ff/Arkansas_Gubernatorial_Election_Results_by_County%2C_2006.svg

HTTP Request: File 41486 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedi


HTTP Request: File 23853 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/1/15/Orion_Ben_Photograph.jpg

HTTP Request: File 14888 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/3/37/Dukes_Lemonade.JPG

HTTP Request: File 37832 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/f/fb/Dead_Space_Logo.jpg

HTTP Request: File 46318 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/8/8f/Yuriko_Koike_cropped.jpg

HTTP Request: File 23869 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/en/7/77/AIIMSRaipur.webp

HTTP Request: File 1057 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/6/6a/Michael_Scott%2C_Athens.jpg

HTTP Request: File 37850 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/8/8b/Bikram_teaching.jpg

HTTP Request: File 28654 Couldn't be re


HTTP Request: File 51214 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/en/6/61/43-Corvus-Constellation.PNG

HTTP Request: File 15219 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/en/a/a8/Normal_CFM_trace.jpg

HTTP Request: File 28808 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/5/53/%E4%B9%9D%E5%8D%8E%E5%B1%B1%E6%9C%80%E5%A4%A7%E7%9A%84%E5%A4%A7%E9%9B%84%E5%AE%9D%E6%AE%BF-1933%E5%B9%B4%E4%BA%8E%E5%8F%B3%E4%BB%BB%E4%B9%A6%E5%8C%BE%E2%80%9C%E5%A4%A7%E9%9B%84%E5%AE%9D%E6%AE%BF%E2%80%9D%EF%BC%8C%E9%A2%98%E8%B5%A0%E7%A5%97%E5%9B%AD%E5%AF%BA%E9%80%80%E5%B1%85%E5%83%A7%E5%AE%BD%E6%89%AC%E3%80%81%E4%BD%8F%E6%8C%81%E5%83%A7%E5%AE%BD%E6%85%88%E3%80%821936%E5%B9%B4_-_panoramio.jpg

Exception downloading as image: 42153
syntax error: line 1, column 0
Offending URL: https://upload.wikimedia.org/wikipedia/commons/0/0b/Delaware_election_results%2C_Senate_1994.svg

HTTP Request: File 20136 Couldn't b

...


HTTP Request: File 1977 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/9/96/Ww2_170.jpg

HTTP Request: File 34512 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/6/6d/Velvaleedickinsonmay201942letter.jpg

HTTP Request: File 29857 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/8/8b/NTHU_Cheng_Kung_Lake_20080204.jpg

HTTP Request: File 10689 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/en/4/43/Keith_Maddison_St.George_Dragons_1967.jpg

HTTP Request: File 52185 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/8/84/Photo_verybig_817184.jpg

HTTP Request: File 47509 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/9/9a/Stamps_of_Ecuador%2C_2009-50.jpg

HTTP Request: File 10704 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/c/c4/Bandera_Nis


HTTP Request: File 11848 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/3/36/Monte_aguila_escudo.png

HTTP Request: File 3235 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/3/3d/Charentsavan.png

HTTP Request: File 21186 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/0/0d/Port_Moresby_parliament_building_front%2C_by_Steve_Shattuck.jpg

HTTP Request: File 3246 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/8/87/General_Simeon_Ola.jpg

HTTP Request: File 3316 Couldn't be retrieved
Offending File: http://upload.wikimedia.org/wikipedia/en/0/01/THESCARYGUY2011B400.jpg

HTTP Request: File 3322 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/3/3c/Logo_expo_2020.gif

HTTP Request: File 30125 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/0/08/2004_Beirut_77933125.jpg

H


HTTP Request: File 52781 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/1/11/2004_Daihatsu_Taruna_FL_1.5_EFI_%28F521RV%3B_03-07-2019%29.jpg

HTTP Request: File 7794 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/6/6c/Angel_Orensanz_Center_004.jpg

HTTP Request: File 16668 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/d/dc/Unknown_Mongolia_-_a_record_of_travel_and_exploration_in_north-west_Mongolia_and_Dzungaria_%281914%29_%2814775986081%29.jpg

HTTP Request: File 21420 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/c/c2/American_star_1994_large.jpg

HTTP Request: File 43927 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/3/3b/Flag_of_Embu_County.png

HTTP Request: File 21429 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/f/f5/Th%C3%A9r%C3%A9sa_Cabarrus.JPG

HTT

HTTP Request: File 8422 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/e/ed/%D8%AE%D9%84%D9%8A%D9%84_%D8%AC%D8%A7%D8%B3%D9%85_%D9%85%D8%B9_%D8%A7%D9%84%D9%85%D9%84%D9%83_%D9%81%D9%8A%D8%B5%D9%84_%D8%A7%D9%84%D8%AB%D8%A7%D9%86%D9%8A_%D9%88%D8%A7%D9%84%D9%88%D8%B5%D9%8A_%D8%B9%D8%A8%D8%AF_%D8%A7%D9%84%D8%A7%D9%84%D9%87.jpg

HTTP Request: File 35471 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/8/8f/Queen_of_Hearts_Signature.jpg

HTTP Request: File 53376 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/b/bb/Bandera_Oneida.PNG

HTTP Request: File 22005 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/6/67/JFKWHP-AR6843-A_%28cropped%29.jpg

HTTP Request: File 35485 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/d/d4/TheTimes_exposes_TheProtocols_as_a_forgery.jpg

HTTP Request: File 26550 Couldn't be retriev


HTTP Request: File 31380 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/en/e/e1/2002_Christadelphian_hymnbook.jpg

HTTP Request: File 22497 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/a/a8/IND_004723.jpg

HTTP Request: File 17728 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/d/d8/08983jfUrdaneta_Zuellig_Building_One_Roxas_Triangle_Paseo_de_Roxas_Gil_Puyat_Makati_Avenuesfvf_05.jpg

HTTP Request: File 53846 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/b/b5/Georgian_license_plate%2C_1983%E2%80%931989_series_with_1989_sticker.png

HTTP Request: File 22511 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/d/da/Work_aboveground_-_mine_02.jpg

HTTP Request: File 27014 Couldn't be retrieved
Offending File: https://upload.wikimedia.org/wikipedia/commons/a/a5/Bandera_Tulalip.png

HTTP Request: File 13263 Couldn't